# 02 - Treinamento do modelo

Neste notebook, objetiva-se treinar e avaliar três diferentes arquiteturas de deep learning. Para isso, utilizaremos aprendizado por transferência em três modelos base:
- **ResNet** (`resnet34`): Uma arquitetura com 34 camadas, reconhecida por suas conexões de atalho (skip-connections) que facilitam o treinamento de redes profundas, equilibrando complexidade e desempenho.
- **EfficientNet** (`efficientnet_b0`): A versão mais leve da família EfficientNet, otimizada para eficiência e precisão, tornando-a ideal para cenários com recursos limitados.
- **MobileNet** (`mobilenetv2_100`): Projetada para aplicações em dispositivos móveis, esta versão emprega convoluções separáveis, resultando em um modelo leve e rápido, sem comprometer a performance na classificação de imagens.

Antes de executar este arquivo, assegure-se de ter o arquivo `data.zip` (gerado no notebook anterior) salvo no diretório `../transfer`. Caso esteja executando no colab, basta fazer o seu upload no diretório atual de trabalho e ele será transferido para o referido diretório.

In [1]:
%%capture

! mkdir -p ../transfer
! mv data.zip ../transfer

Antes de mais nada, vamos verificar se estamos em um ambiente com GPU disponível.

In [2]:
! nvidia-smi

Wed Feb 26 16:40:16 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   38C    P8              9W /   70W |       0MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

## Importações

In [3]:
%%capture

! pip install timm

In [4]:
# Imports relacionados ao PyTorch
import torch
import timm

# Imports para manipulação de dados e transformações
from torchvision import transforms, datasets
from collections import Counter

# Imports para métricas e avaliação de desempenho
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix

# Imports para visualização com Plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio

# Outros imports
import os
import random
import shutil
import numpy as np
from tqdm.notebook import tqdm
from google.colab import files

## Constantes e sets

In [5]:
SEED = 42
DEVICE = 'cuda'
IMAGE_SIZE = (224, 224)
DATA_DIR = '../data/'
MODELS_DIR = '../models'
NUM_EPOCHS = 50
BLUE = '#52B2CF'
RED = '#FF5147'
BLACK = '#0A0A0A'

pio.templates.default = 'plotly'

# Para garantir reprodutibiildade
np.random.seed(SEED)
random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
torch.cuda.manual_seed_all(SEED)  # Para multi-GPU
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

# Função de inicialização do worker para o DataLoader
def seed_worker(worker_id):
    np.random.seed(SEED)
    random.seed(SEED)

## Leitura do dataset

Realizada a preparação dos dados no último notebook, vamos descomprimi-los para utilizar neste notebook.

In [6]:
%%capture

! unzip -o ../transfer/data.zip
! mv data {DATA_DIR}

Feito isto, vamos realizar a leitura e augmentação dos dados.

In [7]:
imagenet_means = [0.485, 0.456, 0.406]  # Média dos canais do ImageNet (base de dados dos modelos base que utilizaremos)
imagenet_stds = [0.229, 0.224, 0.225]  # Desvpad do ImageNet

train_transform = transforms.Compose([
    transforms.Resize((IMAGE_SIZE[0], IMAGE_SIZE[1])),
    # transforms.CenterCrop(IMAGE_SIZE[0]),  # Melhor Resize ou Crop?
    transforms.RandomRotation(20),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize(
        mean=imagenet_means,
        std=imagenet_stds
    )
])

data_transform = transforms.Compose([
    transforms.Resize((IMAGE_SIZE[0], IMAGE_SIZE[1])),
    # transforms.CenterCrop(IMAGE_SIZE[0]),
    transforms.ToTensor(),
    transforms.Normalize(
        mean=imagenet_means,
        std=imagenet_stds
    )
])

train_dataset = datasets.ImageFolder(root=os.path.join(DATA_DIR, 'train'), transform=train_transform)
test_dataset = datasets.ImageFolder(root=os.path.join(DATA_DIR, 'test'), transform=data_transform)

Feito isto, podemos então instanciar os nossos objetos DataLoader que serão utilizados para treinamento e validação/teste.

In [8]:
num_workers = os.cpu_count()  # Para usar o máximo possível
batch_size = 16  # Quanto maior o lote, mais rápido -> Mais paralelismo

train_dataloader = torch.utils.data.DataLoader(
    train_dataset,
    batch_size=batch_size,
    num_workers=num_workers,  # Máximo possível
    worker_init_fn=seed_worker,  # Para garantir reprodutibilidade
    pin_memory=True,  # Acelera o tempo de transferência para GPU
    shuffle=True  # Importante!! A ordem de apresentação dos dados irá impactar no treinamento!
)

test_dataloader = torch.utils.data.DataLoader(
    test_dataset,
    batch_size=batch_size,
    num_workers=num_workers,
    worker_init_fn=seed_worker,
    pin_memory=True,
    shuffle=False  # Para o teste, deixamos como false para que os indices entre o dataloader e o dataset fiquem iguais (importante para a função de sumarização)
)

Antes de partirmos para o treinamento, vamos fazer uma pré-validação para ver quantas categorias existem em cada split.

In [9]:
train_class_counts = dict(Counter(train_dataloader.dataset.targets))
test_class_counts = dict(Counter(test_dataloader.dataset.targets))

train_class_counts, test_class_counts

({0: 140, 1: 140}, {0: 60, 1: 60})

Além disso, podemos verificar visualmente a proporção das classes:

In [10]:
fig_prop = go.Figure()
fig_prop.add_trace(go.Bar(x=list(train_class_counts.keys()), y=list(train_class_counts.values()),
                          name='Treino', marker_color=BLUE))
fig_prop.add_trace(go.Bar(x=list(test_class_counts.keys()), y=list(test_class_counts.values()),
                          name='Validação', marker_color=RED))  # Usando teste como validação devido ao baixo volume de dados
fig_prop.update_layout(barmode='group', title='Proporção das classes em treinamento e validação')
fig_prop.show()

Em que tem-se os seguintes mapas do id para label:

In [11]:
assert train_dataset.class_to_idx == test_dataset.class_to_idx  # Para ter certeza que não vai dar problema
train_dataset.class_to_idx, test_dataset.class_to_idx

({'damaged': 0, 'intact': 1}, {'damaged': 0, 'intact': 1})

## Treinamento

Feito isto, podemos definir algumas funções. A função `epoch` executa uma etapa completa de treinamento de uma rede neural, representando um ciclo integral (uma época) com os dados fornecidos pelo `dataloader`. Já a função `evaluate` calcula as mesmas métricas, mas sem realizar a atualização dos pesos da rede, utilizando igualmente os dados do `dataloader`.

In [12]:
def epoch(model, dataloader, criterion, optimizer):
    model.cuda()  # Move o modelo para GPU
    model.train()  # Seta o modelo para modo de treinamento

    epoch_loss = 0.0  # Será iterado e atualizado
    num_batches = 0  # Idem
    y_true = []
    y_pred = []
    for x, y in tqdm(dataloader, leave=False):
        # Move as entradas e rótulos para a GPU
        x, y = x.cuda(), y.cuda()

        # Limpa os gradientes acumulados da etapa anterior de atualização de pesos
        optimizer.zero_grad()

        # Forward
        logits = model(x)
        pred = logits.argmax(1).flatten().cpu().tolist()
        loss = criterion(input=logits, target=y)

        # Backward
        loss.backward()

        # Atualização dos pesos (w <- w_cur - lr*grad(loss, w))
        optimizer.step()

        # Importante deixar o detach para não estourar a memória (salva só a loss ao invés de todo grafo)
        epoch_loss += loss.detach().cpu().item()
        num_batches += 1

        # Para calcular a acurácia depois
        y_true.extend(y.cpu().tolist())
        y_pred.extend(pred)

    loss = epoch_loss / num_batches
    accuracy = accuracy_score(y_true=y_true, y_pred=y_pred)

    metrics = {
        'accuracy': accuracy,
        'loss': loss
    }

    return metrics

In [13]:
def evaluate(model, dataloader, criterion):
    model.cuda()  # Mover o modelo para a GPU
    model.eval()  # Define o modelo para modo de avaliação

    total_loss = 0.0
    num_batches = 0
    y_true = []
    y_pred = []
    for x, y in tqdm(dataloader, leave=False):  # Acho que fica menos poluído
        # Move as entradas e rótulos para a GPU
        x, y = x.cuda(), y.cuda()

        # Forward
        logits = model(x)
        pred = logits.argmax(1).flatten().cpu().tolist()

        # Calcula a loss
        loss = criterion(input=logits, target=y).detach().cpu().item()  # Já é a loss média do batch
        total_loss += loss
        num_batches += 1

        # Coleta os rótulos verdadeiros e as predições
        y_true.extend(y.cpu().tolist())
        y_pred.extend(pred)

    # Calcula a loss média e a acurácia
    mean_loss = total_loss / num_batches
    accuracy = accuracy_score(y_true=y_true, y_pred=y_pred)

    metrics = {
        'accuracy': accuracy,
        'loss': mean_loss
    }

    return metrics

Além dessas funções, vamos criar uma função que forneça resultados detalhados da classificação de um modelo, incluindo métricas como **recall**, **precision** e **f1-score** para cada classe individualmente, garantindo uma análise mais precisa e completa do desempenho do modelo por rótulo, e uma outra função que sumariza graficamente os resultados do treinamento.

A função `get_classification_summary` foi modificada para processar os dados do `dataloader` individualmente, registro por registro, permitindo maior controle sobre o fluxo de dados. Essa abordagem facilita a separação e o monitoramento das imagens, distinguindo entre aquelas capturadas de cima e de lado, o que permite uma análise mais detalhada dos resultados do modelo para cada perspectiva.

In [14]:
def get_classification_summary(model, dataset, dataloader, class_to_idx_map):
    model.eval()
    model.cuda()

    # Obtendo os caminhos dos arquivos de teste
    file_paths = [fp for fp, _ in dataset.imgs]

    # Obtendo índices para as imagens de topo e lateral
    top_indices = [i for i, f in enumerate(file_paths) if 'top' in f]
    side_indices = [i for i, f in enumerate(file_paths) if 'side' in f]

    # Listas para armazenar as predições e rótulos reais
    top_preds = []
    side_preds = []
    top_real_preds = []
    side_real_preds = []

    c = 0  # Contador para rastrear o índice real
    for images, labels in dataloader:
        # Mover imagens para a GPU
        images = images.cuda()

        for i in range(len(images)):
            logits = model(images[i].unsqueeze(0))
            pred = logits.argmax(1).flatten().cpu().item()

            real_index = i + c  # Índice real da imagem no dataset
            if real_index in top_indices:
                top_real_preds.append(labels[i].cpu().item())
                top_preds.append(pred)  # Adiciona predição
            elif real_index in side_indices:
                side_real_preds.append(labels[i].cpu().item())
                side_preds.append(pred)

        c += len(images)  # Atualiza o contador de índices

    # Resumo geral sem distinção
    all_real_preds = top_real_preds + side_real_preds
    all_preds = top_preds + side_preds

    print('Sumarização de Classificação Geral:')
    print(classification_report(all_real_preds, all_preds, target_names=class_to_idx_map.keys()))
    print('Matriz de Confusão Geral:')
    print(confusion_matrix(all_real_preds, all_preds))

    # Gerando e imprimindo os relatórios de classificação
    print('\nSumarização de Classificação para Imagens de Topo:')
    print(classification_report(top_real_preds, top_preds, target_names=class_to_idx_map.keys()))
    print('Matriz de Confusão para Imagens de Topo:')
    print(confusion_matrix(top_real_preds, top_preds))

    print('\nSumarização de Classificação para Imagens Laterais:')
    print(classification_report(side_real_preds, side_preds, target_names=class_to_idx_map.keys()))
    print('Matriz de Confusão para Imagens Laterais:')
    print(confusion_matrix(side_real_preds, side_preds))

In [15]:
def plot_train_summary(summary):
    epochs = [e + 1 for e in range(len(summary['train_loss']))]

    fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=True)
    # Loss
    fig.add_trace(go.Scatter(x=epochs, y=summary['train_loss'], name='Treino', legendgroup='Treino',
                             marker_color=BLUE, mode='lines'), row=1, col=1)
    fig.add_trace(go.Scatter(x=epochs, y=summary['val_loss'], name='Validação', legendgroup='Validação',
                             marker_color=RED, mode='lines'), row=1, col=2)
    # Acurácia
    fig.add_trace(go.Scatter(x=epochs, y=summary['train_accuracy'], name='Treino', legendgroup='Treino',
                             marker_color=BLUE, mode='lines', showlegend=False), row=2, col=1)
    fig.add_trace(go.Scatter(x=epochs, y=summary['val_accuracy'], name='Validação', legendgroup='Validação',
                             marker_color=RED, mode='lines', showlegend=False), row=2, col=2)
    # Título e nome dos axes
    fig.update_layout(title='Resultados de treinamento', yaxis1_title='Loss', yaxis3_title='Acurácia',
                      xaxis3_title='Época', xaxis4_title='Época')

    fig.show()

Por fim, vamos criar uma função chamada `fit` que irá realizar todo o processo de treinamento.

In [16]:
def fit(model, train_dataloader, val_dataloader, criterion, optimizer, num_epochs=10,
        save_best=False, save_path='.', state_dict_name='state_dict'):
    summary = {
        'train_loss': [],
        'train_accuracy': [],
        'val_loss': [],
        'val_accuracy': [],
    }

    # Caso seja desejado salvar o melhor modelo
    if save_best:
        os.makedirs(save_path, exist_ok=True)

    best_val_accuracy = 0.0  # Melhor acurácia de validação até agora (iterado)
    for e in tqdm(range(num_epochs)):
        print(f'Epoch {e + 1}:')

        # Treinamento
        train_metrics = epoch(model, train_dataloader, criterion, optimizer)
        summary['train_loss'].append(train_metrics['loss'])
        summary['train_accuracy'].append(train_metrics['accuracy'])

        # Avaliação no conjunto de validação
        val_metrics = evaluate(model, val_dataloader, criterion)
        summary['val_loss'].append(val_metrics['loss'])
        summary['val_accuracy'].append(val_metrics['accuracy'])

        print(f'train_loss: {train_metrics["loss"]:.4f} | train_accuracy: {train_metrics["accuracy"]:.4f} | '
              f'val_loss: {val_metrics["loss"]:.4f} | val_accuracy: {val_metrics["accuracy"]:.4f}')

        # Salvar o estado do modelo se a acurácia de validação melhorar
        if val_metrics['accuracy'] > best_val_accuracy:
            best_val_accuracy = val_metrics['accuracy']

            if save_best:
                model_save_path = os.path.join(save_path, f'{state_dict_name}.torch')
                torch.save(model.state_dict(), model_save_path)
                print(f'New best! Saving state dict to {model_save_path}')

        print('-' * shutil.get_terminal_size().columns)  # Imprime '-' até completar a largura do console

    return summary

### Resnet

Para este caso, utilizaremos o modelo de id `resnet34` que corresponde a uma versão de 34 camadas da ResNet, conhecida por suas conexões de atalho que facilitam o treinamento de redes profundas, equilibrando complexidade e desempenho.

In [17]:
resnet_id = 'resnet34'

resnet = timm.create_model(resnet_id, pretrained=True, num_classes=len(train_dataloader.dataset.classes))
resnet_criterion = torch.nn.CrossEntropyLoss(weight=None)
resnet_optimizer = torch.optim.Adam(resnet.parameters(), lr=1E-3)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning:


The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.



model.safetensors:   0%|          | 0.00/87.3M [00:00<?, ?B/s]

In [18]:
resnet_summary = fit(resnet, train_dataloader, test_dataloader, resnet_criterion, resnet_optimizer,
                     NUM_EPOCHS, save_best=True, save_path=MODELS_DIR, state_dict_name=f'{resnet_id}-state_dict')

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 1:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.7047 | train_accuracy: 0.4643 | val_loss: 0.6829 | val_accuracy: 0.5167
New best! Saving state dict to ../models/resnet34-state_dict.torch
----------------------------------------------------------------------------------------------------
Epoch 2:


...

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.2483 | train_accuracy: 0.9107 | val_loss: 1.2270 | val_accuracy: 0.6500
----------------------------------------------------------------------------------------------------
Epoch 50:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.3037 | train_accuracy: 0.8679 | val_loss: 0.9449 | val_accuracy: 0.5917
----------------------------------------------------------------------------------------------------


In [19]:
plot_train_summary(resnet_summary)

In [20]:
resnet_state_dict = torch.load(os.path.join(MODELS_DIR, f'{resnet_id}-state_dict.torch'), weights_only=True)
resnet.load_state_dict(resnet_state_dict)

get_classification_summary(resnet, test_dataset, test_dataloader, test_dataset.class_to_idx)

Sumarização de Classificação Geral:
              precision    recall  f1-score   support

     damaged       0.69      0.75      0.72        60
      intact       0.73      0.67      0.70        60

    accuracy                           0.71       120
   macro avg       0.71      0.71      0.71       120
weighted avg       0.71      0.71      0.71       120

Matriz de Confusão Geral:
[[45 15]
 [20 40]]

Sumarização de Classificação para Imagens de Topo:
              precision    recall  f1-score   support

     damaged       0.58      0.63      0.60        30
      intact       0.59      0.53      0.56        30

    accuracy                           0.58        60
   macro avg       0.58      0.58      0.58        60
weighted avg       0.58      0.58      0.58        60

Matriz de Confusão para Imagens de Topo:
[[19 11]
 [14 16]]

Sumarização de Classificação para Imagens Laterais:
              precision    recall  f1-score   support

     damaged       0.81      0.87      0.84  

### EfficientNet

Aqui utilizaremos a `efficientnet_b0`, uma versão mais leve da família EfficientNet, otimizada para eficiência e precisão, ideal para cenários com recursos limitados.

In [21]:
efficientnet_id = 'efficientnet_b0'


efficientnet = timm.create_model(efficientnet_id, pretrained=True, num_classes=len(train_dataloader.dataset.classes))
efficientnet_criterion = torch.nn.CrossEntropyLoss(weight=None)
efficientnet_optimizer = torch.optim.Adam(efficientnet.parameters(), lr=1E-3)

model.safetensors:   0%|          | 0.00/21.4M [00:00<?, ?B/s]

In [22]:
efficientnet_summary = fit(efficientnet, train_dataloader, test_dataloader, efficientnet_criterion, efficientnet_optimizer,
                           NUM_EPOCHS, save_best=True, save_path=MODELS_DIR, state_dict_name=f'{efficientnet_id}-state_dict')

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 1:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 4.9209 | train_accuracy: 0.5107 | val_loss: 3.9922 | val_accuracy: 0.5083
New best! Saving state dict to ../models/efficientnet_b0-state_dict.torch
----------------------------------------------------------------------------------------------------
Epoch 2:


...

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.4263 | train_accuracy: 0.8250 | val_loss: 0.7098 | val_accuracy: 0.6750
----------------------------------------------------------------------------------------------------
Epoch 50:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.3590 | train_accuracy: 0.8286 | val_loss: 0.7056 | val_accuracy: 0.6833
----------------------------------------------------------------------------------------------------


In [23]:
plot_train_summary(efficientnet_summary)

In [24]:
efficientnet_state_dict = torch.load(os.path.join(MODELS_DIR, f'{efficientnet_id}-state_dict.torch'), weights_only=True)
efficientnet.load_state_dict(efficientnet_state_dict)

get_classification_summary(efficientnet, test_dataset, test_dataloader, test_dataset.class_to_idx)

Sumarização de Classificação Geral:
              precision    recall  f1-score   support

     damaged       0.75      0.65      0.70        60
      intact       0.69      0.78      0.73        60

    accuracy                           0.72       120
   macro avg       0.72      0.72      0.72       120
weighted avg       0.72      0.72      0.72       120

Matriz de Confusão Geral:
[[39 21]
 [13 47]]

Sumarização de Classificação para Imagens de Topo:
              precision    recall  f1-score   support

     damaged       0.58      0.50      0.54        30
      intact       0.56      0.63      0.59        30

    accuracy                           0.57        60
   macro avg       0.57      0.57      0.56        60
weighted avg       0.57      0.57      0.56        60

Matriz de Confusão para Imagens de Topo:
[[15 15]
 [11 19]]

Sumarização de Classificação para Imagens Laterais:
              precision    recall  f1-score   support

     damaged       0.92      0.80      0.86  

### MobileNet

Por fim, optaremos pela `mobilenetv2_100`, um modelo projetado para aplicações em dispositivos móveis. Esta versão utiliza convoluções separáveis, o que a torna leve e rápida, enquanto mantém uma boa performance na classificação de imagens. Além disso, é o mesmo modelo utilizado no Teachable Machine.

In [25]:
mobilenet_id = 'mobilenetv2_100'

mobilenet = timm.create_model(mobilenet_id, pretrained=True, num_classes=len(train_dataloader.dataset.classes))
mobilenet_criterion = torch.nn.CrossEntropyLoss(weight=None)
mobilenet_optimizer = torch.optim.Adam(mobilenet.parameters(), lr=1E-3)

model.safetensors:   0%|          | 0.00/14.2M [00:00<?, ?B/s]

In [26]:
mobilenet_summary = fit(mobilenet, train_dataloader, test_dataloader, mobilenet_criterion, mobilenet_optimizer,
                        NUM_EPOCHS, save_best=True, save_path=MODELS_DIR, state_dict_name=f'{mobilenet_id}-state_dict')

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 1:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 4.0985 | train_accuracy: 0.5321 | val_loss: 4.9033 | val_accuracy: 0.5000
New best! Saving state dict to ../models/mobilenetv2_100-state_dict.torch
----------------------------------------------------------------------------------------------------
Epoch 2:


...

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.3437 | train_accuracy: 0.8464 | val_loss: 0.7239 | val_accuracy: 0.6667
----------------------------------------------------------------------------------------------------
Epoch 50:


  0%|          | 0/18 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

train_loss: 0.2993 | train_accuracy: 0.8500 | val_loss: 0.9658 | val_accuracy: 0.6500
----------------------------------------------------------------------------------------------------


In [27]:
plot_train_summary(mobilenet_summary)

In [28]:
mobilenet_state_dict = torch.load(os.path.join(MODELS_DIR, f'{mobilenet_id}-state_dict.torch'), weights_only=True)
mobilenet.load_state_dict(mobilenet_state_dict)

get_classification_summary(mobilenet, test_dataset, test_dataloader, test_dataset.class_to_idx)

Sumarização de Classificação Geral:
              precision    recall  f1-score   support

     damaged       0.82      0.60      0.69        60
      intact       0.68      0.87      0.76        60

    accuracy                           0.73       120
   macro avg       0.75      0.73      0.73       120
weighted avg       0.75      0.73      0.73       120

Matriz de Confusão Geral:
[[36 24]
 [ 8 52]]

Sumarização de Classificação para Imagens de Topo:
              precision    recall  f1-score   support

     damaged       0.57      0.27      0.36        30
      intact       0.52      0.80      0.63        30

    accuracy                           0.53        60
   macro avg       0.55      0.53      0.50        60
weighted avg       0.55      0.53      0.50        60

Matriz de Confusão para Imagens de Topo:
[[ 8 22]
 [ 6 24]]

Sumarização de Classificação para Imagens Laterais:
              precision    recall  f1-score   support

     damaged       0.93      0.93      0.93  

Treinado os modelos, vamos exportá-los para o diretório de transferência para utilizá-los em outra sessão.

In [29]:
%%capture

! zip -ro ../transfer/models.zip {MODELS_DIR}

E para facilitar, vamos baixar o arquivo final (caso esteja rodando no Colab).

In [30]:
files.download('../transfer/models.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Conclusões

Após o treinamento dos três modelos, observou-se uma clara melhoria na acurácia do conjunto de treinamento, acompanhada por uma redução na loss, sendo essas alterações mais pronunciadas do que nas métricas de teste. Essa discrepância indica uma defasagem e aponta para uma possível tendência ao overfitting, especialmente se o número de épocas for incrementado. Todavia, é importante ressaltar que as curvas de loss e especialmente da acurácia de validação apresentaram um padrão de "dentes de serra", refletindo a influência do número limitado de amostras de teste, o que levou a variações consideráveis nas métricas com pequenas modificações no modelo. Essa situação torna desafiadora a avaliação da evolução da acurácia em teste à medida que se aumentam as épocas de treinamento.

Tomando os melhores modelos encontrados com base na acurácia, observou-se que o **MobileNet** obteve o melhor desempenho em teste, alcançando a maior acurácia e f1-score médio. Todavia, os resultados alcançados pelo **EfficientNet** e **ResNet** foram próximos a este, não sendo possível descartá-los.

Observando os valores de recall, foi possível verificar que o **EfficientNet** obteve o maior valor para a classe `damaged`, demonstrando sua eficácia em identificar embalagens danificadas. Em contraste, a **MobileNet** obteve o maior valor de recall em `intact`, indicando que este modelo teve uma maior confiabilidade em classificar corretamente as embalagens intactas.

Já com relação a perspectiva das imagens, foi possível verificar que os modelos tiveram maiores acurácias ao classificar as imagens obtidas pela lateral (_side_) dos objetos, sendo os valores aqui encontrados consideravelmente maiores que quando classificados pelo topo (_top_). Além disso, observou-se que o recall das classes, em todas as arquiteturas, foi igual ou superior ao analisar os objetos pela lateral em comparação com a vista superior.

Por último, é importante ressaltar que, apesar das análises realizadas, não é possível afirmar qual o melhor modelo, visto que isto não deve se restringir apenas às métricas técnicas, sendo necessário ter um entendimento mais profundo do negócio para identificar quais aspectos são mais críticos a serem classificados corretamente.